In [0]:
%run ../_utils

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
  Using cached Unidecode-1.3.8-py3-none-any.whl (235 kB)
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
from pyspark.sql.functions import when, to_date, col, dayofweek
from pyspark.sql.types import StringType, BooleanType


# Camada Silver

Na camada silver, limpezas e ajustes em dados devem ser aplicados

Caso seja possível, enriquecer os dados e extrair dados também deve acontecer nessa camada (minha definição)

In [0]:
tb_name = "olist_silver.products"
dataset_location = "olist_products_dataset"
target_location = f"dbfs:/FileStore/delta/brazilian_ecommerce/{dataset_location}/silver"

## 1 - Data ingestion

In [0]:
df = spark.read.table("olist_bronze.products") # leituira da delta table

In [0]:
df.printSchema()

root
 |-- product_id: string (nullable = true)
 |-- product_category_name: string (nullable = true)
 |-- product_name_lenght: integer (nullable = true)
 |-- product_description_lenght: integer (nullable = true)
 |-- product_photos_qty: integer (nullable = true)
 |-- product_weight_g: integer (nullable = true)
 |-- product_length_cm: integer (nullable = true)
 |-- product_height_cm: integer (nullable = true)
 |-- product_width_cm: integer (nullable = true)



In [0]:
display(df)

product_id product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm 1e9e8ef04dbcff4541ed26657ea517e5 perfumaria 40 287 1 225 16 10 14 3aa071139cb16b67ca9e5dea641aaa2f artes 44 276 1 1000 30 18 20 96bd76ec8810374ed1b65e291975717f esporte_lazer 46 250 1 154 18 9 15 cef67bcfe19066a932b7673e239eb23d bebes 27 261 1 371 26 4 26 9dc1a7de274444849c219cff195d0b71 utilidades_domesticas 37 402 4 625 20 17 13 41d3672d4792049fa1779bb35283ed13 instrumentos_musicais 60 745 1 200 38 5 11 732bd381ad09e530fe0a5f457d81becb cool_stuff 56 1272 4 18350 70 24 44 2548af3e6e77a690cf3eb6368e9ab61e moveis_decoracao 56 184 2 900 40 8 40 37cc742be07708b53a98702e77a21a02 eletrodomesticos 57 163 1 400 27 13 17 8c92109888e8cdf9d66dc7e463025574 brinquedos 36 1156 1 600 17 10 12 14aa47b7fe5c25522b47b4b29c98dcb9 cama_mesa_banho 54 630 1 1100 16 10 16 03b63c5fc16691530586ae020c345514 bebes 49 728 4 7150 50 19 45 cf55509ea8edaaac1d28fdb16e48fc22 instrumentos_musicais 43 1827 3 250 17 7 17 7bb6f29c2be57716194f96496660c7c2 moveis_decoracao 51 2083 2 600 68 11 13 eb31436580a610f202c859463d8c7415 construcao_ferramentas_seguranca 59 1602 4 200 17 7 17 3bb7f144022e6732727d8d838a7b13b3 esporte_lazer 22 3021 1 800 16 2 11 6a2fb4dd53d2cdb88e0432f1284a004c perfumaria 39 346 2 400 27 5 20 a1b71017a84f92fd8da4aeefba108a24 informatica_acessorios 59 636 1 900 40 15 20 a0736b92e52f6cead290e30b578413b6 moveis_decoracao 56 296 2 1700 100 7 15 f53103a77d9cf245e579ea37e5ec51f0 cama_mesa_banho 52 206 1 500 16 10 16 1c1890ba1779090cd54008a3c3302921 moveis_decoracao 27 158 4 2550 29 24 45 518ef5de2c2b3a255e326a4594ba15d9 cama_mesa_banho 27 329 2 800 36 8 16 e3e020af31d4d89d2602272b315c3f6e beleza_saude 58 1987 3 75 21 7 13 8b41fbc2b984a12030090112324d1bc4 bebes 55 1627 1 500 20 13 13 d03bd02af9fff4b98f1c972315e5e9ef moveis_decoracao 56 209 1 1800 40 10 30 8ba4f2a4ae695d26e5626c1bf710975e utilidades_domesticas 52 968 1 900 50 5 50 f6574524b07d5bb753bab6f35abe2d06 malas_acessorios 52 573 5 3600 35 25 50 c78b767da00efb70c1bcccab87c28cd5 informatica_acessorios 35 1101 2 300 42 2 30 a0253d43394dd4da9a5d7b1f546f1a32 informatica_acessorios 59 1890 2 740 23 13 13 051b9ff13dd55c0a6655a15ff296f80d esporte_lazer 50 529 2 3600 62 23 23 47859fca9dd7485cbd93c3e8993bb74f cama_mesa_banho 45 206 1 650 16 10 16 e1d1d22e9f8122a4ec1533b032c12562 ferramentas_jardim 49 1163 9 2150 70 8 34 20e37962088a4061d3578def47a8648b moveis_decoracao 60 208 1 800 40 10 34 1eba879220bd0981a0e2fbab499ed4e1 moveis_escritorio 57 476 1 8950 52 51 17 ce5b91848b91118daffb3af53b747475 esporte_lazer 50 699 4 1388 34 9 31 5370b82a213393979691c98074265584 bebes 52 708 9 7950 33 30 44 b8dac5113b06a97e64943234522572b9 automotivo 43 1062 2 6000 87 3 42 750cf819d127191920eda79a4b6fb479 eletronicos 31 806 1 263 18 12 16 e6af694343b45b56304ad91974a110b9 utilidades_domesticas 37 352 1 3900 19 20 15 680874c570dad71c0a2844cfbf417054 moveis_decoracao 47 502 1 600 25 25 25 8b3a9476f74f5297f7ff0ec6d95fe1ea moveis_decoracao 63 254 2 2050 49 13 41 1c6fb703c624b381a20f21f757694866 brinquedos 33 471 2 725 22 17 15 db46052aed7dff59ba38cf2fe29b87f9 cama_mesa_banho 56 509 4 6350 45 15 35 b864b103180d5a6a3f830e67f93e8735 bebes 47 980 4 600 70 11 11 7a8dac4aaa16bc642e4df33adcf03303 cool_stuff 38 1701 2 11750 18 40 79 83b9bc6aae6f527ff6aafb9e01d6cbf3 brinquedos 20 866 3 2550 22 32 38 5f504b3a1c75b73d6151be81eb05bdc9 cool_stuff 38 1176 3 15350 47 40 47 bbf920aa6ac72007a726e6f419156f8f moveis_decoracao 42 303 2 1300 25 16 25 c3b7e4d83e530c27a8e6368296aece48 moveis_decoracao 60 1972 2 850 69 11 11 c5d8079278e912d7e3b6beb48ecb56e8 beleza_saude 60 330 1 1300 19 28 17 5eaa343860dc445b3fd43d1b682809fd esporte_lazer 53 3218 5 4800 60 30 15 b5cfb1d3c5e435a7a52227e08f220ee7 cool_stuff 55 410 2 1300 36 16 24 334479e94cba98064050db1c9636e244 automotivo 57 311 1 220 18 14 17 3fcd8dfe610c62edfb51de2630cd9ef4 bebes 50 509 4 5700 41 17 49 4c8056caed5757810b9a68b83c375


## 2 - Data Cleaning

Aqui nessa table os dados já estão limpos e tratados. só iremos armazenar a silver (nao precisa nem do product_category_name_translation)


## Saving data

In [0]:
save_dataframe(df, format_mode="delta", table_name=tb_name, target_location=target_location)

[LOG] Saving olist_silver.products delta on dbfs:/FileStore/delta/brazilian_ecommerce/olist_products_dataset/silver... OK!



## create delta table

TODO: implementar UPSERT

o upsert serve para não precisar reescrever todos os dados, mas aproveitar do Delta para fazer um MERGE, caso um registro antigo tenha uma nova versão e INSERT para os dados que são novos

In [0]:
create_table(table_name=tb_name, target_location=target_location)

[LOG] Creating delta table olist_silver.products on dbfs:/FileStore/delta/brazilian_ecommerce/olist_products_dataset/silver... OK!


In [0]:
display(df)

product_id product_category_name product_name_lenght product_description_lenght product_photos_qty product_weight_g product_length_cm product_height_cm product_width_cm 1e9e8ef04dbcff4541ed26657ea517e5 perfumaria 40 287 1 225 16 10 14 3aa071139cb16b67ca9e5dea641aaa2f artes 44 276 1 1000 30 18 20 96bd76ec8810374ed1b65e291975717f esporte_lazer 46 250 1 154 18 9 15 cef67bcfe19066a932b7673e239eb23d bebes 27 261 1 371 26 4 26 9dc1a7de274444849c219cff195d0b71 utilidades_domesticas 37 402 4 625 20 17 13 41d3672d4792049fa1779bb35283ed13 instrumentos_musicais 60 745 1 200 38 5 11 732bd381ad09e530fe0a5f457d81becb cool_stuff 56 1272 4 18350 70 24 44 2548af3e6e77a690cf3eb6368e9ab61e moveis_decoracao 56 184 2 900 40 8 40 37cc742be07708b53a98702e77a21a02 eletrodomesticos 57 163 1 400 27 13 17 8c92109888e8cdf9d66dc7e463025574 brinquedos 36 1156 1 600 17 10 12 14aa47b7fe5c25522b47b4b29c98dcb9 cama_mesa_banho 54 630 1 1100 16 10 16 03b63c5fc16691530586ae020c345514 bebes 49 728 4 7150 50 19 45 cf55509ea8edaaac1d28fdb16e48fc22 instrumentos_musicais 43 1827 3 250 17 7 17 7bb6f29c2be57716194f96496660c7c2 moveis_decoracao 51 2083 2 600 68 11 13 eb31436580a610f202c859463d8c7415 construcao_ferramentas_seguranca 59 1602 4 200 17 7 17 3bb7f144022e6732727d8d838a7b13b3 esporte_lazer 22 3021 1 800 16 2 11 6a2fb4dd53d2cdb88e0432f1284a004c perfumaria 39 346 2 400 27 5 20 a1b71017a84f92fd8da4aeefba108a24 informatica_acessorios 59 636 1 900 40 15 20 a0736b92e52f6cead290e30b578413b6 moveis_decoracao 56 296 2 1700 100 7 15 f53103a77d9cf245e579ea37e5ec51f0 cama_mesa_banho 52 206 1 500 16 10 16 1c1890ba1779090cd54008a3c3302921 moveis_decoracao 27 158 4 2550 29 24 45 518ef5de2c2b3a255e326a4594ba15d9 cama_mesa_banho 27 329 2 800 36 8 16 e3e020af31d4d89d2602272b315c3f6e beleza_saude 58 1987 3 75 21 7 13 8b41fbc2b984a12030090112324d1bc4 bebes 55 1627 1 500 20 13 13 d03bd02af9fff4b98f1c972315e5e9ef moveis_decoracao 56 209 1 1800 40 10 30 8ba4f2a4ae695d26e5626c1bf710975e utilidades_domesticas 52 968 1 900 50 5 50 f6574524b07d5bb753bab6f35abe2d06 malas_acessorios 52 573 5 3600 35 25 50 c78b767da00efb70c1bcccab87c28cd5 informatica_acessorios 35 1101 2 300 42 2 30 a0253d43394dd4da9a5d7b1f546f1a32 informatica_acessorios 59 1890 2 740 23 13 13 051b9ff13dd55c0a6655a15ff296f80d esporte_lazer 50 529 2 3600 62 23 23 47859fca9dd7485cbd93c3e8993bb74f cama_mesa_banho 45 206 1 650 16 10 16 e1d1d22e9f8122a4ec1533b032c12562 ferramentas_jardim 49 1163 9 2150 70 8 34 20e37962088a4061d3578def47a8648b moveis_decoracao 60 208 1 800 40 10 34 1eba879220bd0981a0e2fbab499ed4e1 moveis_escritorio 57 476 1 8950 52 51 17 ce5b91848b91118daffb3af53b747475 esporte_lazer 50 699 4 1388 34 9 31 5370b82a213393979691c98074265584 bebes 52 708 9 7950 33 30 44 b8dac5113b06a97e64943234522572b9 automotivo 43 1062 2 6000 87 3 42 750cf819d127191920eda79a4b6fb479 eletronicos 31 806 1 263 18 12 16 e6af694343b45b56304ad91974a110b9 utilidades_domesticas 37 352 1 3900 19 20 15 680874c570dad71c0a2844cfbf417054 moveis_decoracao 47 502 1 600 25 25 25 8b3a9476f74f5297f7ff0ec6d95fe1ea moveis_decoracao 63 254 2 2050 49 13 41 1c6fb703c624b381a20f21f757694866 brinquedos 33 471 2 725 22 17 15 db46052aed7dff59ba38cf2fe29b87f9 cama_mesa_banho 56 509 4 6350 45 15 35 b864b103180d5a6a3f830e67f93e8735 bebes 47 980 4 600 70 11 11 7a8dac4aaa16bc642e4df33adcf03303 cool_stuff 38 1701 2 11750 18 40 79 83b9bc6aae6f527ff6aafb9e01d6cbf3 brinquedos 20 866 3 2550 22 32 38 5f504b3a1c75b73d6151be81eb05bdc9 cool_stuff 38 1176 3 15350 47 40 47 bbf920aa6ac72007a726e6f419156f8f moveis_decoracao 42 303 2 1300 25 16 25 c3b7e4d83e530c27a8e6368296aece48 moveis_decoracao 60 1972 2 850 69 11 11 c5d8079278e912d7e3b6beb48ecb56e8 beleza_saude 60 330 1 1300 19 28 17 5eaa343860dc445b3fd43d1b682809fd esporte_lazer 53 3218 5 4800 60 30 15 b5cfb1d3c5e435a7a52227e08f220ee7 cool_stuff 55 410 2 1300 36 16 24 334479e94cba98064050db1c9636e244 automotivo 57 311 1 220 18 14 17 3fcd8dfe610c62edfb51de2630cd9ef4 bebes 50 509 4 5700 41 17 49 4c8056caed5757810b9a68b83c375

In [0]:
# exit para fechar a execução
dbutils.notebook.exit("OK")

In [0]:
%sql

select * from olist_bronze.products